<center><img src="images/banner_part_1.png" align="center"/></center>

## 1. Exploración y analisis
Muchos de los servicios principales de MELI son públicos, lo cual permite acceder a los datos de forma sencilla. En la primera parte del desafío el objetivo es realizar un análisis exploratorio de las publicaciones con descuento del marketplace. Las preguntas a responder y el enfoque del análisis son libres. Como punto de partida se puede sugiere utilizar la API de search de mercadolibre, la cual está por detrás del buscador de Mercadolibre.

En esta parte del desafío, las preguntas son abiertas, pero a modo de ayuda estas son algunas de las que se podrían responder:
* ¿Cual es el descuento promedio en distintas categorías del marketplace?
* ¿Cuántos productos con descuento tenemos en televisores? ¿y en celulares?


### 1.1. Categorías y subcategorías

Arrancamos revisando cómo están distribuidos los servicios de MercadoLibre. En particular, vale mencionar los identificadores de cada uno de los `sites` o portales de MercadoLibre para cada país. Así, el identificador de Argentina es MLA, el de Chile es MLC y el de Colombia es MCO [[ver listado completo]](https://api.mercadolibre.com/sites). El presente desarrollo está basado en el site de MercadoLibre para Colombia, con código MCO.

Enseguida, notamos que el sitio cuenta con categorías ("Carros, Motos y Otros" , "Computación" , "Celulares y Teléfonos",...) y subcategorías para cada una de las primeras (para la categoría "Celulares y Teléfonos" hay subcategorías como "Accesorios para Celulares", "Celulares y Smartphones", "Repuestos de Celulares",...). Cada categoría y subcategoría cuenta con un identificador único que inicia con los caracteres "MCO".

Entonces, lo primero que haremos será elegir algunas subcategorías, traernos los datos aprovechando los atributos en su API, armar un dataframe y trabajar en el análisis:

In [1]:
# Para cargar las librerías que usaremos

import pandas as pd    # Para el manejo de dataframes
import numpy as np     # Para algunas operaciones numéricas
import requests        # Para las solicitudes a la API
import json            # Para trabajar con formatos JSON 
from pandas.io.json import json_normalize      # Para aplanar los JSON y convertirlos en DataFrame
import plotly.express as px                    # Para gráficos sencillos pero elegantes e interactivos
import pandas_profiling as pf                  # Para facilitar el análisis descriptivo y exploratorio

In [2]:
# Para traer todo el listado de categorías:
file_json = requests.get("https://api.mercadolibre.com/sites/MCO/categories").json() # Para hacer la solicitud "GET" a la API y tomar la parte de los datos en formato JSON
categories = pd.DataFrame(file_json)                                                 # Para convertir en dataframe los datos traídos
display(categories[10:20])                                                           # Para desplegar el listado de categorías

id                         name
10    MCO1743        Carros, Motos y Otros
11    MCO1051        Celulares y Teléfonos
12    MCO1648                  Computación
13    MCO1144       Consolas y Videojuegos
14    MCO1276           Deportes y Fitness
15    MCO5726            Electrodomésticos
16    MCO1000   Electrónica, Audio y Video
17  MCO175794  Herramientas y Construcción
18    MCO1574              Hogar y Muebles
19    MCO1499        Industrias y Oficinas

Nos iremos con la categoría **"Celulares y Teléfonos"**. Ahora, buscaremos una subcategoría interesante.

In [3]:
def subcategories(MCO):                                                        # Función para mostrar una tabla con las subcategorías a partir del MCO
    subcategories_df = requests.get("https://api.mercadolibre.com/categories/" + str(MCO)).json()
    subcategories_df = pd.DataFrame(subcategories_df["children_categories"])   # Dentro del JSON, children_categories es la key asociada a las subcategorías
    return(subcategories_df)

In [4]:
subcategories("MCO1051")

id                          name  total_items_in_this_category
0    MCO3813     Accesorios para Celulares                        820404
1    MCO1055       Celulares y Smartphones                         38639
2  MCO401278     Gafas de Realidad Virtual                           945
3    MCO1058              Radios y Handies                         19989
4  MCO442202        Repuestos de Celulares                         72470
5  MCO417704     Smartwatches y Accesorios                         57757
6   MCO10616       Tarificadores y Cabinas                          1113
7    MCO1053  Telefonía Fija e Inalámbrica                          6517
8    MCO5237                  Telefonía IP                          2947
9    MCO1915                         Otros                          9484

Considerando la razonable cantidad de ítems y su relevancia para los compradores en línea, aquí trabajaremos con **"Celulares y Smartphones"**. Su identificador es MCO1055.

Ahora repetimos el proceso para otra subcategoría interesante pero ahora en la categoría **"Electrónica, Audio y Video"**:

In [5]:
subcategories("MCO1000")

id                      name  total_items_in_this_category
0     MCO3690  Accesorios Audio y Video                         79071
1   MCO431414        Accesorios para TV                         64620
2     MCO3835                     Audio                        438991
3     MCO5054                    Cables                        205215
4    MCO11830  Componentes Electrónicos                        183703
5     MCO4632         Controles Remotos                         54741
6   MCO176837  Convertidores a Smart TV                          6654
7   MCO173235       Drones y Accesorios                         66915
8   MCO442042           Fundas y Bolsos                          1487
9     MCO4102        Pilas y Cargadores                         43323
10  MCO419930              Repuestos TV                         16687
11   MCO14903               Televisores                         12447
12  MCO442056                     Video                         16492
13    MCO4800   Video Beams y Pantallas                         38320
14    MCO1070                     Otros                         48179

**"Televisores"** parece interesante por lo que trabajaremos con ella siendo su código el MCO14903. Complementaremos con **"Video Beams y Pantallas"**, **"Accesorios Audio y Video"** y **"Smartwatches y Accesorios"** (MCO4800, MCO3690 y MCO417704, respectivamente): son de temática similar y se han hecho más necesarios que nunca con el tema de la pandemia.

En resumen, fueron 5 los elegidos:

* MCO1055: Celulares y Teléfonos/Celulares y Smartphones/    
* MCO417704: Celulares y Teléfonos/Smartwatches y Accesorios
* MCO14903: Electrónica, Audio y Video/Televisores
* MCO4800: Electrónica, Audio y Video/Video Beams y Pantallas
* MCO3690: Electrónica, Audio y Video/Accesorios Audio y Video

### 1.2. Generación del dataset
Ya con los códigos elegidos, resta armar el dataset inicial yendo a consultar a la API de MercadoLibre directamente con dichos códigos:

In [6]:
selected_codes = {"MCO1055": "cellphones", "MCO417704":"smartwatches", "MCO14903": "televisions", "MCO4800": "screens", "MCO3690":"audio"}

¿Cuántos registros hay por cada código?

In [7]:
for code in selected_codes.keys():
    registros =  requests.get("https://api.mercadolibre.com/sites/MCO/search?category="+ code).json()['paging']['total'] # Número total de registros
    print(code, selected_codes[code], str("-> " + str(registros) + " registros"))

MCO1055 cellphones -> 37405 registros
MCO417704 smartwatches -> 69709 registros
MCO14903 televisions -> 11749 registros
MCO4800 screens -> 38226 registros
MCO3690 audio -> 75514 registros


<div class="alert-info">
    Para considerar:
</div>

Aunque sería interesante hacerlo con toda la data, para evitar potenciales limitaciones en tiempo y acceso al recurso, solo tomaremos 1.000 registros por código MCO. Para ello, recurriremos a los parámetros `limit` y `offset` proveídos por la API <a href= "https://developers.mercadolibre.com.ar/en_us/paging-results">[Más información] </a>

In [8]:
n = 1000 # registros por categoría
import requests
from requests_oauthlib import OAuth1

auth = OAuth1('7393870389611734',
  '7pFsN44Pif4o8J1PZnQ4m1dsZkQMF86Z',
  'localhost',
  'MCO'
)

final_base = pd.DataFrame()

for code in selected_codes.keys():
    base = pd.DataFrame()
    for i in range(0, n, 50):             
        items = requests.get("https://api.mercadolibre.com/sites/MCO/search?category="+ code + "&offset=" + str(i) + 
                             "&limit=50", auth=auth).json()      # Para armar las URL       
        items = pd.json_normalize(items['results'])              # Para "aplanar" los JSON
        base = base.append(items, ignore_index=True)             # Reiniciar índices
        base['sub_cat'] = selected_codes[code]
    final_base = final_base.append(base, ignore_index=True)  
    base.to_csv("data/"+ selected_codes[code] + ".csv", sep='|', encoding = "utf-8") #Exportar resultados por si no se desea llamar la API cada vez

<div class="alert-info">
Por mejorar:
</div>

Para traer más de 1.000 registros, hay [otra forma]("https://developers.mercadolibre.com.co/es_ar/items-y-busquedas#Modo-de-busqueda-por-encima-de-1000-registros") de realizar la búsqueda. Queda pendiente su implementación para futuros trabajos.
        


Y así ya tenemos la base final, con 5.000 registros de nuestros interés, 1.000 por cada una de las categorías elegidas:

In [9]:
print(final_base.shape)
final_base.sample(5)

(5000, 58)


id site_id                                              title  \
2271  MCO587867745     MCO              Televisor LG 49lj550t Para Repuestos    
1052  MCO566816459     MCO  Manilla Pulsera Correa Repuesto Para Smart Ban...   
1825  MCO595444566     MCO  Funda Carcasa Protector Para Huawei Gt 2 46mm Tpu   
1291  MCO566305377     MCO  Vidrio Templado Apple Watch + Estuche Funda 38...   
4058  MCO532410983     MCO  Adaptador De Audio Optico A Rca Analogo + Cabl...   

       price sale_price currency_id  available_quantity  sold_quantity  \
2271  450000       None         COP                   1              0   
1052    3990       None         COP                 250            200   
1825   18990       None         COP                  50              5   
1291   19900       None         COP                   1             50   
4058   22800       None         COP                   1            150   

     buying_mode listing_type_id  ... seller_address.state.id  \
2271  buy_it_now    gold_special  ...                  CO-TOL   
1052  buy_it_now    gold_special  ...                   CO-DC   
1825  buy_it_now    gold_special  ...                   CO-DC   
1291  buy_it_now        gold_pro  ...                   CO-DC   
4058  buy_it_now    gold_special  ...                   CO-DC   

     seller_address.state.name seller_address.city.id  \
2271                    Tolima       TUNPQ0lCQTI0NzNh   
1052               Bogotá D.C.       TUNPQ1VTQTY3MTQ1   
1825               Bogotá D.C.       TUNPQ0VORzkzMTUz   
1291               Bogotá D.C.       TUNPQ0FOVDMyNjIx   
4058               Bogotá D.C.       TUNPQ1JBRjkyNTA2   

     seller_address.city.name  seller_address.latitude  \
2271                   Ibagué                            
1052                  Usaquén                            
1825                 Engativá                            
1291           Antonio Nariño                            
4058       Rafael Uribe Uribe                            

     seller_address.longitude       sub_cat differential_pricing.id  \
2271                            televisions                     NaN   
1052                           smartwatches                     NaN   
1825                           smartwatches                     NaN   
1291                           smartwatches              33602181.0   
4058                                  audio                     NaN   

     installments prices  
2271          NaN    NaN  
1052          NaN    NaN  
1825          NaN    NaN  
1291          NaN    NaN  
4058          NaN    NaN  

[5 rows x 58 columns]

## 1.3 Análisis de variables



Lo más importante es tener en cuenta el **objetivo del análisis**, en este caso, extraer conocimiento desde las publicaciones en diferentes categorías de productos. Una buena idea es realizar un análisis para conocer las distribuciones de cada variable, sus categorías y sus tipos así como revisar datos atípicos, datos faltantes y relaciones entre ellas.

In [10]:
final_base.dtypes

id                              object
site_id                         object
title                           object
price                            int64
sale_price                      object
currency_id                     object
available_quantity               int64
sold_quantity                    int64
buying_mode                     object
listing_type_id                 object
stop_time                       object
condition                       object
permalink                       object
thumbnail                       object
accepts_mercadopago               bool
attributes                      object
original_price                  object
category_id                     object
official_store_id               object
domain_id                       object
catalog_product_id              object
tags                            object
order_backend                    int64
seller.id                        int64
seller.permalink                object
seller.registration_date 

In [11]:
# Para crear un reporte analizando todas las variables en conjunto
profile = pf.ProfileReport(final_base)
profile

### Diagnóstico general 
* Duplicados: Hay 5.000 registros únicos pero hay un par de registros repetidos por ID
* Más de la mitad de variables (36/58) son categóricas. No hay filas vacías pero sí filas con celdas vacías.
* 15 variables solo tiene un valor constante destacando de ellas accept_mercadopago (en todas las publicaciones se acepta mercadopago), la verificación de que todo está en pesos colombianos y variables completamente vacías ("") como latitud y longitud. [Ver sección _Warnings_ en el informe]


### Variables en general 
* Hay 4.955 publicaciones con imágenes únicas, al menos en su URL.
* Alrededor de 4.700 tienen títulos únicos
* Las publicaciones vienen de 151 ciudades diferentes.
* El 25% de las publicaciones no tienen ventas (valor cero en sold_quantity).
* Variables como las etiquetas, no se aplanaron correctamente, por lo que requieren limpieza para su uso.

### Valores perdidos y correlaciones

<center><img src="images/missing.png" align="center"/></center>
El gráfico específica la cantidad de valores nulos por variable. Se destaca que sale_price está completamente sin datos, original_price tiene 92.5% de valores nulos, prices está totalmente vacía y solo el 5.7% tienen valor en original_price (o sea, solo ese porcentaje son publicaciones con descuento). 

<center><img src="images/correlations.png" align="center"/></center>

Muchas de las correlaciones son triviales y se infieren por el nombre, por ejemplo, la correlación entre todas las variables de ubicación (address), sin embargo, a la hora de modelar, sí vale la pena echarle un vistazo más detallado a correlaciones entre numéricas, en especial, a todas las relacionadas con precios y ventas (incluyendo la correlación entre original_price y sold_quantity ).

### Más insights
* El 92.4% son productos nuevos.
* El 56.4% son publicaciones de Bogotá, seguido por Antioquia con un 12.2% y un 9.2% de Cundinamarca.
* El 68.1% aparece con envío gratuito.
* Localidades de Bogotá (Engativá) superan a ciudades tan grandes como Medellín, Cali y Bucaramanga.

In [12]:
# Estadísticas básicas sobre el precio por categoría
final_base.groupby("sub_cat")['price'].describe().reset_index()

sub_cat   count         mean           std     min        25%  \
0         audio  1000.0   100021.165  2.475867e+05  1100.0   14511.75   
1    cellphones  1000.0  1054653.817  1.398103e+06  2000.0  329900.00   
2       screens  1000.0  2278707.711  1.187533e+07  1000.0  229975.00   
3  smartwatches  1000.0   121794.851  2.921248e+05  1500.0   17900.00   
4   televisions  1000.0  2248734.081  8.703760e+06  1000.0  435675.00   

        50%        75%          max  
0   34700.0    99225.0    4510990.0  
1  699900.0  1099900.0   21999000.0  
2  503945.0  1254247.5  216204000.0  
3   36189.5   115217.5    2399000.0  
4  989900.0  1800000.0  200000000.0

In [28]:
# Para generar la variable descuento (recordando que las publicaciones con descuento son las que tienen valor en original price)
final_base['discount'] = (final_base['original_price'] / final_base['price']) - 1
final_base['discount'] = final_base['discount'].astype(float)

In [29]:
# Subconjunto de la base solo con las publicaciones con descuento
discounts_base = final_base[final_base['original_price'].notnull()]  
discounts_base.shape

(284, 59)

In [38]:
discounts_base.groupby('sub_cat')['discount'].agg("mean").sort_values(ascending = False)

sub_cat
televisions     0.482202
smartwatches    0.388795
cellphones      0.366908
audio           0.319209
screens         0.193325
Name: discount, dtype: float64

In [39]:
fig = px.histogram(discounts_base, x="discount", facet_col = "sub_cat")
fig.show()

De las consideradas, el descuento promedio más alto está en la categoría/subcategoría "Televisores", seguido de la categoría de "Smartwatches". Sin embargo, el que más productos con descuentos tiene es la categoría "Celulares y Smartphones" (16.6%), como se puede notar en el eje Y de los histogramas y como se verifica en la siguiente tabla:

In [48]:
final_base['discount_h'] = np.where(pd.notnull(final_base['discount']), 1,0)
percentage_base = final_base.groupby(['sub_cat'])['discount_h'].agg(["sum", "count"])
percentage_base['perc'] = (percentage_base['sum']/percentage_base['count'])*100
percentage_base

sum  count  perc
sub_cat                       
audio           9   1000   0.9
cellphones    166   1000  16.6
screens         9   1000   0.9
smartwatches   24   1000   2.4
televisions    76   1000   7.6

### Extra: Siguientes pasos y mejoras al código:
* Tryerror: Por ejemplo, para controlar que los parámetros OFFSET y LIMIT recorran todo pero sigan funcionando en caso de que una categoría tenga menos registros de los muestreados.
* Considerar una población más amplia y recurrir a las propiedades de la aleatoriedad para correr pruebas inferenciales que permitan probar hipótesis más complicadas cuyas pruebas se basan en distribuciones estadísticas.
* Recurrir a un tablero en Dash para añadir más interactividad a las visualizaciones y hacer más cómoda la publicación de los resultados.